In [10]:
from sklearn.svm import LinearSVC
from sklearn.datasets import load_iris
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.preprocessing import LabelEncoder, StandardScaler
import pandas as pd
import numpy as np

In [2]:
musicData = pd.read_csv('dataset/data-v1.csv')
print(musicData.shape)
print(musicData.head())

FileNotFoundError: [Errno 2] No such file or directory: 'data.csv'

In [157]:

X = musicData[['chroma_stft','rmse','spectral_centroid','spectral_bandwidth','rolloff', 'zero_crossing_rate', 'mfcc1', 'mfcc2',
                'mfcc3','mfcc4','mfcc5','mfcc6','mfcc7','mfcc8','mfcc9','mfcc10','mfcc11','mfcc12','mfcc13','mfcc14','mfcc15','mfcc16',
                'mfcc17','mfcc18','mfcc19','mfcc20']].values 
y = musicData[['label']].values



#label encoding
#from sklearn import preprocessing
#le = preprocessing.LabelEncoder()

#le.fit(["blues", "classical", "country", "disco", "hiphop", "jazz", "metal", "pop", "reggae", "rock"])
#list(le.classes_)
#ylabelled = le.transform(y)



X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, shuffle = True)

# Data normalization
scaler = StandardScaler()
scaler.fit(X_train)

X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

In [158]:
lsvc = LinearSVC(max_iter=100000, dual = False)
print(lsvc)

LinearSVC(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=100000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0)


In [159]:
lsvc.fit(X_train, y_train.ravel())
score = lsvc.score(X_train, y_train.ravel())
print("Score: ", score)

cv_scores = cross_val_score(lsvc, X_train, y_train.ravel(), cv=10)
print("CV average score: %.2f" % cv_scores.mean())

ypred = lsvc.predict(X_test)

cm = confusion_matrix(y_test, ypred)
print(cm)

cr = classification_report(y_test, ypred)
print(cr) 

Score:  0.6825
CV average score: 0.60
[[ 8  0  0  1  1  3  1  0  0  2]
 [ 0 19  1  0  0  0  0  0  1  0]
 [ 0  0 14  1  0  0  2  0  1  3]
 [ 0  0  1 12  0  0  2  3  3  1]
 [ 1  0  0  1  9  1  0  4  3  0]
 [ 1  3  3  1  0 17  0  0  0  0]
 [ 0  0  0  1  1  1 15  1  0  2]
 [ 2  0  0  3  0  1  0  9  0  0]
 [ 0  0  0  1 10  1  0  0  8  0]
 [ 2  1  3  3  0  1  3  0  0  7]]
              precision    recall  f1-score   support

       blues       0.57      0.50      0.53        16
   classical       0.83      0.90      0.86        21
     country       0.64      0.67      0.65        21
       disco       0.50      0.55      0.52        22
      hiphop       0.43      0.47      0.45        19
        jazz       0.68      0.68      0.68        25
       metal       0.65      0.71      0.68        21
         pop       0.53      0.60      0.56        15
      reggae       0.50      0.40      0.44        20
        rock       0.47      0.35      0.40        20

    accuracy                       

In [11]:
import librosa
import IPython.display as ipd

###
songname = './data/Booba-Rapti_World.mp3'
###

ipd.Audio(songname)


In [12]:
y, sr = librosa.load(songname, mono=True, duration=60)
chroma_stft = librosa.feature.chroma_stft(y=y, sr=sr)
spec_cent = librosa.feature.spectral_centroid(y=y, sr=sr)
spec_bw = librosa.feature.spectral_bandwidth(y=y, sr=sr)
rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr)
rmse = librosa.feature.rms(y=y)
zcr = librosa.feature.zero_crossing_rate(y)
mfcc = librosa.feature.mfcc(y=y, sr=sr)

/usr/local/anaconda3/lib/python3.7/site-packages/librosa/core/audio.py:161: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn('PySoundFile failed. Trying audioread instead.')


In [13]:
#create array
songdata = np.array([np.mean(chroma_stft), np.mean(rmse), np.mean(spec_cent), np.mean(spec_bw), np.mean(rolloff), np.mean(zcr)])
for e in mfcc:
    songdata = np.append(songdata, np.mean(e))

In [14]:
songdata = songdata.reshape(1, -1)
songpred = lsvc.predict(songdata)
print(songpred)

NameError: name 'lsvc' is not defined

In [20]:
import tensorflow as tf
from tensorflow import keras

model_path = "./models/musicgenre_nn_classifier_v1.h5"
# model.save(model_path)
model = keras.models.load_model(model_path)
model.predict(songdata)

array([[0., 0., 0., 1., 0., 0., 0., 0., 0., 0.]], dtype=float32)